# **【项目003】数据准备（Data Preparation）** <span style="font-size:16px;"><a style="font-weight:bold;color:red;" href="Project003DataPreparationStudent.html">学生版</a> | <a href="Project003DataPreparationTeaching.html">教学版</a> | <a href="Project003DataPreparation.html">发布版</a> | <a href="http://deeplearning.ouxinyu.cn">返回首页</a></span>

<span style="color:blue;">作者：欧新宇（Xinyu OU）</span>  
<span style="color:blue;">当前版本：Release v1.0 </span>  
<span style="color:blue;">开发平台：Paddle 2.3.2</span>  
<span style="color:blue;">运行环境：Intel Core i7-7700K CPU 4.2GHz, nVidia GeForce GTX 1080 Ti</span>  
<span style="color:red;">本教案所涉及的数据集仅用于教学和交流使用，请勿用作商用。</span>

**最后更新：2022年12月31日**

---

## **【实验目的】**
1. 学会对下载的数据集进行基本的分析和了解
2. 能够按照规范的结构对自建数据集进行整理和规范
3. 能够使用Python编写代码，实现对规范结构数据集进行列表生成，并按照训练集、验证集、训练验证集和测试集进行划分
4. 对非规范数据能够进行规范化处理, 或按照规范标准对数据集进行划分
5. 对不干净的数据，能够编写Python代码进行数据清洗

## **【实验内容】**

***垃圾分类数据集Garbage*** 是一个包含有40个类别，14802张图像的数据集。该数据集已经事先实现了`训练(train)`和`测试(test)`的分割，其中测试集**没有类别**标签。数据集没有给出验证集的划分建议，因此在进行数据列表生成的时候，可以自行按照一定的比列来将官方提供的训练集看作是**trainval**进行二次划分，即将原来的 `train` 文件夹划分为训练集train和验证集val。使用train和val完成训练之后，再按照训练获得超参数，对**整个**训练验证集trainval进行训练，完成后直接输出 `测试集结果` 到平台进行评估。注意，本数据集给出了类别的标签字典，因此在生成和划分数据子集的时候，建议考虑基于该类别标签字典而非遍历文件夹的方式来完成。

<div style="text-align:center;">
    <img src="../../Images/Datasets/Garbage.png" width="800px" title="垃圾分类数据集Garbage" alt="垃圾分类数据集Garbage" />
</div>

### **【实验一】参数初始化（20分）**

- **实验难度**: 简单
- **实验摘要**: 编写Python代码，定义数据数据输入路径及标签输出文件
- **实验目标**：
    1. 学会观察已经下载的数据集，并对其进行基本分析，判断预处理方法；
    2. 根据判断设置文件读取方法和输出方法。  
- **实验要求** 
    1. Q1-1: 完成输出参数的初始化, 包括训练、验证、测试和训练验证集的数量，类别数量和数据集信息文件dataset_info的初始化 ([Your codes 1])（10分）     
    2. Q2-1: 定义生成文件的路径，包括四个列表文件和数据集信息文件，此外还包括需要读入的类别字典`garbage_dict`，用于保存到数据集信息文件dataset_info中 ([Your codes 2])（10分）

In [5]:
##################################################################################
# 数据集预处理
# 作者: Xinyu Ou (http://ouxinyu.cn)
# 数据集名称：垃圾分类数据集Garbage
# 数据集简介: 数据集包含40个类别，其中训练样本14402张，测试样本400张。
# 本程序功能:
# 1. 在训练集中抽取10%的样本作为验证数据集
# 2. 代码将生成4个带标注的列表文件：train, val, trainval, test
# 3. 数据集基本信息：数据集的基本信息使用json格式进行输出，包括数据库名称、数据样本的数量、类别数以及类别标签
###################################################################################

import os
import json
import codecs

#########################################################
# 1. 超参数的初始化 [Q1-1]
# [Your codes 1] 





# 设置图片的前缀，即图像根目录下的子目录路径
train_prefix = 'train'  # train_prefix = val_prefix = trainval_prefix  
test_prefix = 'test'

#########################################################
# 2. 数据集相关路径定义。本地运行时，需要修改数据集的名称和绝对路径，注意和文件夹名称一致。
# 2.1 数据集源路径定义
dataset_name = 'Garbage'
dataset_path = 'D:\\Workspace\\ExpDatasets\\'
dataset_root_path = os.path.join(dataset_path, dataset_name)
exclusion = ['.DS_Store', '.ipynb_checkpoints']    # 被排除的文件夹

# 2.2 数据集输出路径定义 [Q2-1]
# [Your codes 2]




garbage_dict_path = os.path.join(dataset_root_path, 'garbage_dict.json')

# 2.3 检测数据集列表是否已经存在，如果存在则先删除。
# 在Garbage数据集中，测试集只需要一次性写入，可以通过'w'参数进行覆盖写入，而不用进行手动删除。
if os.path.exists(train_list):
    os.remove(train_list)
if os.path.exists(val_list):
    os.remove(val_list)
if os.path.exists(trainval_list):
    os.remove(trainval_list)
if os.path.exists(dataset_info_list):
    os.remove(dataset_info_list)

# 2.4 从官方文件garbage_dict.json获取类别标签
with open(garbage_dict_path, 'r', encoding='utf-8') as f_dict:
    garbage_dict = json.load(f_dict)

# 2.5 读取数据清洗获得的坏样本列表，并将坏文件写入列表以备后续排除（本例可忽略）

### **【实验二】数据集划分（60分）**

- **实验难度**: 困难
- **实验摘要**: 编写Python代码，实现数据集四个子集列表的生成。
- **实验目标**：
    1. 学会根据预先给出的文件存储结构，选择合适的文件读取和输入方式，例如本例中的前缀方法;
    2. 能够对测试集按照顺序进行列表生成;
    3. 能够将数据集划分为训练集、验证集、测试集和训练验证集。
- **实验要求**： 
  1. Q3-1: 完成生成测试列表的代码 ([Your codes 3]) （30分）  
由于测试集的输出结果需要输送到AIStudio进行准确度评估，因此需要对测试集样本严格按照数字从小到大的顺序进行排序。然而，python文件读取时排序方法是按照文本进行排序的，即："test1, test10, test11, test12, ..., test2, test20, ..."，而正确的排序应该是"test1, test2, test3, ..., test10, test11, test12, ..., test20, test21, ..."，即自然顺序。  <font style="color:red;">提示：可以先获取测试文件的`数字`部分，然后对其进行排序，再组合文件名输出到测试文件列表`test.txt`中</font>  
  1. Q3-2: 完成生成训练集、验证集和训练验证集列表的代码, 要求选择10%的原始训练数据用于生成val验证子集，剩下的90%生成train训练子集 ([Your codes 4])（30分）*


In [6]:
#########################################################
# 3. 生成四个不同的数据子集列表
# 3.1 生成测试集列表 [Q3-1]
# 特别注意，因测试集的输出结果需要使用专门的系统进行评估（AIStudio），因此测试集样本列表需要对文件严格按照数字从小到大进行排序
# [Your codes 3]




        
# 3.2 生成训练集、验证集和训练验证集列表 [Q3-2]
# [Your codes 4]





### **【实验三】结果输出（20分）**

- **实验难度**: 中等
- **实验摘要**: 编写Python代码，实现数据划分结果和统计信息的输出
- **实验目标**：
  1. 学会使用json文件完成数据的收集和输出;
  2. 能够在屏幕上打印出有意义的统计信息。
- **实验要求**：   
  1. Q4-1: 完成生成数据集信息的json文件 ([Your codes 5])。（10分）*  
    注意，类别字典在数据集中已经由`garbage_dict`文件给出，且无法从文件夹命名中获取，因此在写入数据集信息的 `label_dict`字段时，需要从 `garbage_dict.json`文件中读取。
  2. Q4-2：在屏幕上输出统计信息 ([Your codes 6])，格式如下: （10分）* 
  > 图像列表已生成, 其中训练验证集样本14402，训练集样本12944个, 验证集样本1458个, 测试集样本400个, 共计14802个。


In [2]:
#########################################################
# 4. 输出统计结果
# 4.1 将数据集信息保存到json文件中供训练和部署使用 [Q4-1]
# 数据集信息包括：数据集名称，训练、验证、测试及训练验证集的样本数量、类别的数量和类别字典
# [Your codes 5] 





# 4.2.输出数据集信息到json文件
with codecs.open(dataset_info_list, 'w', encoding='utf-8') as f_dataset_info:
    json.dump(dataset_info, f_dataset_info, ensure_ascii=False, indent=4, separators=(',', ':')) # 格式化字典格式的参数列表

# 4.3 在控制台中打印数据集基本统计信息 [Q4-2]
# 注意为方便可视化，考虑使用display()替代print()对字典进行输出，但display()只支持notebook接口。
# [Your codes 6] 


